In [1]:
import re
import os
from glob import glob

from langchain_chroma import Chroma
from langchain_core.documents import Document
from langchain.prompts import ChatPromptTemplate
from langchain_core.runnables import RunnablePassthrough
from langchain_openai import OpenAIEmbeddings, ChatOpenAI
from langchain_core.output_parsers import StrOutputParser
from langchain_community.document_loaders import PyMuPDFLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

from dotenv import load_dotenv
load_dotenv()

True

In [2]:
CHUNK_SIZE = 1000
CHUNK_OVERLAP = 0
MODEL_NAME  = 'gpt-4o-mini'
EMBEDDING_NAME = 'text-embedding-3-large'

COLLECTION_NAME = 'korean_history'
PERSIST_DIRECTORY= 'vector_store/korean_history_db'
category = ["사건", "인물"]
name = ["고대", "고려", "근대", "조선", "현대"]

In [3]:
# Split
splitter = RecursiveCharacterTextSplitter.from_tiktoken_encoder(
    model_name=MODEL_NAME,
    chunk_size=CHUNK_SIZE,
    chunk_overlap=CHUNK_OVERLAP,
)

In [ ]:
# db 생성
for j in category:
    for i in name:
        file = glob(f"./pdf/{j}/{i}/*.pdf")
        document_list = []
        for path in file:
            loader = PyMuPDFLoader(path)
            load_docs = loader.load()
            full_text = [doc.page_content for doc in load_docs] 
            full_text = ''.join(full_text)
            full_text = re.sub(r"관련사료", "", full_text)
            full_text = re.sub(r"\([一-龥]+\)", "", full_text)
            full_text = re.sub(r"\n", "", full_text)

            docs = splitter.split_text(full_text)
            id = "_".join(os.path.splitext(os.path.basename(path))[0].split('_')[:2])
            title = os.path.splitext(os.path.basename(path))[0].split('_')[-1]
            metadata = {
            "id":id,
            "title": title,
            "full_text": full_text
            }

            for doc in docs:
                _doc = Document(metadata=metadata, page_content=doc)
                document_list.append(_doc)

        embedding_model = OpenAIEmbeddings(model=EMBEDDING_NAME)

        vector_store = Chroma.from_documents(
            documents=document_list,
            embedding=embedding_model,
            collection_name=COLLECTION_NAME,
            persist_directory=PERSIST_DIRECTORY
        )

        print(len(document_list))

121
114
335
391
175
236
326
381
692
21


In [5]:
# db 연결
embedding_model = OpenAIEmbeddings(model=EMBEDDING_NAME)
vector_store = Chroma(collection_name=COLLECTION_NAME, persist_directory=PERSIST_DIRECTORY, embedding_function=embedding_model)

In [6]:
vector_store._collection.count()

2792

In [7]:
vector_store.get()

{'ids': ['0fe026cf-f3ca-4427-8d0c-9c7f0d4d93fa',
  '6b3d4732-41f8-472a-82cc-49a8bab1d189',
  '61ab8ba4-5714-4889-85cf-28fd3b37add7',
  'e317d2c2-d7d0-4a6a-865b-2d678fe0d1c7',
  'b94301bf-abf0-461a-bf68-e3458071e0e8',
  '21bbc68f-7937-436f-b609-9bf4d18c4c19',
  'bf58f18e-3cb5-43ea-9ee0-3bae69c34b1f',
  'fa542d70-6680-4ee4-b319-7faedcdaba59',
  'ac04cb5d-08bb-4525-ad9b-a0f222492c73',
  'bb21ad6e-ce53-4587-85dc-8c2679ee9304',
  'd0a1bd55-03b3-45b6-8e17-209bec1aad22',
  '9c6447a2-0297-479b-8f82-4ff71a52181e',
  '3c6f4bf5-3213-4514-898e-ab087d984b95',
  '43847757-9015-4ce3-b14c-77e3ef86d3e8',
  'db3d4cf9-0116-4de4-be41-ae31e51dd00b',
  '5c22b0d2-2e55-4b16-9df0-0e2f607ca4bd',
  'efa32815-edbb-4eb6-8f7d-0e0f2c2742df',
  '7a00919b-f983-4bae-8667-cc4ac9015264',
  'b7b65be9-d7f4-457b-8b78-95edd4a95fcf',
  '511b0fc1-7688-4202-a40e-157d131e2339',
  '7707ac45-0cec-4989-84e4-70cba266baed',
  '3ce05874-b129-48be-a5b7-c0017ccab360',
  '45f1fe91-f3e5-49f1-a878-c81c211d0758',
  'eba09cd7-793a-4c91-8eab-

In [8]:
result = vector_store.similarity_search_with_score(
    query="이순신에 대해 알려줘",
    k=5
)
result

[(Document(metadata={'full_text': '이순신[李舜臣]백전백승, 백의종군1545년(인종 1) ~ 1598년(선조 31) 이순신의 생애1545(인종 1)∼1598(선조 31). 조선의 무신이다. 무신으로 등용된 초기에는 북방 오랑캐를 방어하는 데 활약하였고, 일찍부터 장수로서 능력을 인정받았다. 그러나 원칙과 소신이 분명한 성격으로 인해 그를 질시하는 이들이 적지 않았다. 임진왜란 직전 우수한 장수로 특별히 발탁되어 전라좌수영에서 수군을 기르며 전쟁가능성에 대비했다. 전쟁이 발발하자 탁월한 전략, 전술적 능력을 발휘하여 연전연승했다. 이는 꾸준한 준비와 상황에 맞는 적절한 대응책 덕분이기도 했다. 그의 승리 덕분에 조선은 나라를 보전할 수 있었다. 그러나 빛나는 전공은 그를 질시하는 세력의견제를 불러왔고, 이로 인해 삼도수군통제사에서 물러나게 되었다. 하지만 곧 자리에 복귀하여무너진 수군을 재건했고 또 다시 일본군을 격파하였다. 노량해전에서 퇴각을 꾀하던 일본군에맞서 싸우다가 전사했다. 이순신의 유년기와 무신으로의 발탁12명종에서 선조로 이어지는 시기는 성리학을 깊이 익힌 사림들이 자신들의 학문을 정치로 펼치기위해 노력하던 시기였다. 북방 여진족과 남쪽의 왜구들이 조선의 국경을 침범하기도 했지만 그들보다 우수한 장수들이 이들을 격퇴하는 한편으로 무역과 관직수여를 통해 이들을 달래는 방책을 병행하기도 했다.이순신의 본관은 덕수. 자는 여해이다. 아버지는 이정이며, 어머니는 변수림(卞守琳)의 딸이다. 조부 이백록이 기묘사화에 희생된 이후 가세가 기울었으며, 그의 부친은관직에 뜻을 두지 않았다. 그러나 가풍은 엄격하였으며 학문과 문학적인 부분을 소홀히 하지 않았다. 특히 이순신의 어머니는 아들들을 아끼고 사랑하면서도 가정교육을 철저히 하였다. 정의감에 가득 차 불의를 참지 못하나 약한 자에게는 따뜻하게 대하던 이순신의 성격은 이러한 교육에 영향을 받았을 것이다.1572년에 훈련원에서 시행된 무과 별과시험에 응시하였으나 불행히도 말에서 떨어져 실

In [9]:
retriever = vector_store.as_retriever(search_type="mmr")
query = "이순신에 대해 알려줘"
result = retriever.invoke(query)
result

[Document(metadata={'full_text': '이순신[李舜臣]백전백승, 백의종군1545년(인종 1) ~ 1598년(선조 31) 이순신의 생애1545(인종 1)∼1598(선조 31). 조선의 무신이다. 무신으로 등용된 초기에는 북방 오랑캐를 방어하는 데 활약하였고, 일찍부터 장수로서 능력을 인정받았다. 그러나 원칙과 소신이 분명한 성격으로 인해 그를 질시하는 이들이 적지 않았다. 임진왜란 직전 우수한 장수로 특별히 발탁되어 전라좌수영에서 수군을 기르며 전쟁가능성에 대비했다. 전쟁이 발발하자 탁월한 전략, 전술적 능력을 발휘하여 연전연승했다. 이는 꾸준한 준비와 상황에 맞는 적절한 대응책 덕분이기도 했다. 그의 승리 덕분에 조선은 나라를 보전할 수 있었다. 그러나 빛나는 전공은 그를 질시하는 세력의견제를 불러왔고, 이로 인해 삼도수군통제사에서 물러나게 되었다. 하지만 곧 자리에 복귀하여무너진 수군을 재건했고 또 다시 일본군을 격파하였다. 노량해전에서 퇴각을 꾀하던 일본군에맞서 싸우다가 전사했다. 이순신의 유년기와 무신으로의 발탁12명종에서 선조로 이어지는 시기는 성리학을 깊이 익힌 사림들이 자신들의 학문을 정치로 펼치기위해 노력하던 시기였다. 북방 여진족과 남쪽의 왜구들이 조선의 국경을 침범하기도 했지만 그들보다 우수한 장수들이 이들을 격퇴하는 한편으로 무역과 관직수여를 통해 이들을 달래는 방책을 병행하기도 했다.이순신의 본관은 덕수. 자는 여해이다. 아버지는 이정이며, 어머니는 변수림(卞守琳)의 딸이다. 조부 이백록이 기묘사화에 희생된 이후 가세가 기울었으며, 그의 부친은관직에 뜻을 두지 않았다. 그러나 가풍은 엄격하였으며 학문과 문학적인 부분을 소홀히 하지 않았다. 특히 이순신의 어머니는 아들들을 아끼고 사랑하면서도 가정교육을 철저히 하였다. 정의감에 가득 차 불의를 참지 못하나 약한 자에게는 따뜻하게 대하던 이순신의 성격은 이러한 교육에 영향을 받았을 것이다.1572년에 훈련원에서 시행된 무과 별과시험에 응시하였으나 불행히도 말에서 떨어져 실격

In [10]:
retriever = vector_store.as_retriever(search_type="mmr")
# Prompt Template 생성
messages = [
        ("ai", """
    너는 한국사에 대해서 해박한 지식을 가진 역사전문가야.
    내가 역사적 인물 또는 사건에 대해 말하면 그 인물과 사건을 이해가 쉽게, 흥미를 잃지 않게 쉬운용어로 풀어서 설명해주면 돼.

    문서에 없는 내용은 답변할 수 없습니다. 모른다고 답변 하세요.

    인물의 이름 :
    시대 :
    인물에 대해 알고 싶은 것 :
{context}"""),
        ("human", "{question}"),
    ]
prompt_template = ChatPromptTemplate(messages)

# 모델
model = ChatOpenAI(model="gpt-4o-mini")

# output parser
parser = StrOutputParser()

# Chain 구성 retriever(관련 문서 조회) -> prompt_template(prompt 생성) model(정답) -> output parser
chain = {"context":retriever, "question":RunnablePassthrough()} | prompt_template | model | parser

In [11]:
result = chain.invoke("나옹혜근에 대해 알려줘") # 나옹혜근

In [12]:
print(result)

죄송하지만, "나옹혜근"에 대한 정보는 제공된 문서에 없습니다. 다른 역사적 인물이나 사건에 대해 질문해주시면 기꺼이 도와드리겠습니다.


In [13]:
# https://www.dinolabs.ai/394
# pip install gTTS

In [14]:
from gtts import gTTS
from IPython.display import Audio
from IPython.display import display

In [12]:
tts = gTTS(result, lang='ko')
tts.save('result.mp3')

wn = Audio(filename='result.mp3', autoplay=True)
display(wn)